In [1]:
import numpy as np
import xarray as xr
from dask.distributed import Client
from dask_jobqueue import SLURMCluster 
import gsw

In [2]:
# Define needed variables
glorys_archive_dir = '/archive/e1n/datasets/GLORYS/monthly_means/'
glorys_dir = "/work/role.medgrp/NEP/plotting/Figure_4/"
year = 1993

In [3]:
# Get mask file
ds_glorys_mask =  xr.open_dataset((glorys_dir + 'glorys_nep_mask.nc'),decode_times=False)
bathym = ds_glorys_mask.deptho.values
#bathym = ds_glorys_mask.deptho

In [4]:
portdash = 11412
cluster = SLURMCluster(scheduler_options={"dashboard_address": f":{portdash}"})

2025-04-30 12:37:54,390 - distributed.scheduler - ERROR - Couldn't gather keys: {('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 175, 33, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 182, 16, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 284, 27, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 253, 23, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 161, 1, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 192, 5, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 74, 0, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 56, 27, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 87, 31, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 174, 32, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 91, 41, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 263, 12, 0, 0): 'waiting', ('sigma0-41ae696ecdbbf4a7d9299e728c41a984', 221, 7, 0, 0): 'waiting', ('si

In [5]:
cluster.scale(1)
client = Client(cluster)
client

<Client: 'tcp://140.208.147.176:43883' processes=0 threads=0, memory=0 B>

In [6]:
# Dmget and stage files
#! for year in {1993..1996} ; do dmget /archive/e1n/datasets/GLORYS/monthly_means/GLORYS_REANALYSIS_NEP_${year}-*.tmp.nc ; done
#! module load gcp ; for year in {1993..1996} ; do echo "Working on ${year}"; gcp --cd --sync /archive/e1n/datasets/GLORYS/monthly_means/GLORYS_REANALYSIS_NEP_${year}-*.tmp.nc /xtmp/Utheri.Wagura/work/GLORYS/ ; done
#! module load gcp ; for year in {1993..1996} ; do echo "Working on ${year}"; gcp --cd --sync /archive/e1n/datasets/GLORYS/monthly_means/GLORYS_REANALYSIS_NEP_${year}-*.tmp.nc ${TMPDIR}/GLORYS/ ; done

# Confirm that it worked
#! ls /xtmp/Utheri.Wagura/GLORYS/work/

In [7]:
# Open staged files
#g_ds = xr.open_mfdataset("/xtmp/Utheri.Wagura/work/GLORYS/GLORYS_REANALYSIS_NEP_????-??.tmp.nc")
g_ds = xr.open_mfdataset("/xtmp/Utheri.Wagura/work/GLORYS/GLORYS_REANALYSIS_NEP_1993-??.tmp.nc")
g_ds

<xarray.Dataset> Size: 298GB
Dimensions:    (time: 324, depth: 50, latitude: 865, longitude: 1321)
Coordinates:
  * depth      (depth) float32 200B 0.494 1.541 2.646 ... 5.275e+03 5.728e+03
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
  * time       (time) datetime64[ns] 3kB 1993-01-16T12:00:00 ... 2019-12-16T1...
Data variables:
    so         (time, depth, latitude, longitude) float32 74GB dask.array<chunksize=(1, 1, 865, 1321), meta=np.ndarray>
    thetao     (time, depth, latitude, longitude) float32 74GB dask.array<chunksize=(1, 1, 865, 1321), meta=np.ndarray>
    uo         (time, depth, latitude, longitude) float32 74GB dask.array<chunksize=(1, 1, 865, 1321), meta=np.ndarray>
    vo         (time, depth, latitude, longitude) float32 74GB dask.array<chunksize=(1, 1, 865, 1321), meta=np.ndarray>
    zos        (time, latitude, longitude) float32 1GB dask.array<chunksize=(1, 865, 1321), meta=np.ndarray>
Attributes: (12/28)
    CDI:                                Climate Data Interface version 2.1.1 ...
    Conventions:                        CF-1.4
    source:                             MERCATOR GLORYS12V1
    institution:                        MERCATOR OCEAN
    title:                              daily mean fields from Global Ocean P...
    easting:                            longitude
    ...                                 ...
    FROM_ORIGINAL_FILE__latitude_max:   90.0
    z_min:                              0.494025
    z_max:                              5727.917
    _CoordSysBuilder:                   ucar.nc2.dataset.conv.CF1Convention
    NCO:                                netCDF Operators version 5.1.5 (Homep...
    CDO:                                Climate Data Operators version 2.1.1 ...

In [8]:
# calculate potential density for that month and repackage as xarray dataset
pot_density = gsw.density.sigma0(g_ds["so"], g_ds["thetao"])
pot_density

<xarray.DataArray 'so' (time: 324, depth: 50, latitude: 865, longitude: 1321)> Size: 148GB
dask.array<sigma0, shape=(324, 50, 865, 1321), dtype=float64, chunksize=(1, 1, 865, 1321), chunktype=numpy.ndarray>
Coordinates:
  * depth      (depth) float32 200B 0.494 1.541 2.646 ... 5.275e+03 5.728e+03
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
  * time       (time) datetime64[ns] 3kB 1993-01-16T12:00:00 ... 2019-12-16T1...
Attributes:
    standard_name:  sea_water_salinity
    long_name:      Salinity
    units:          1e-3
    unit_long:      Practical Salinity Unit
    cell_methods:   area: mean time: mean
    _ChunkSizes:    [  1   7 341 720]

In [9]:
# Interpret density to 5m
potdens_5m = pot_density.interp(depth=5.0)
potdens_5m

<xarray.DataArray 'so' (time: 324, latitude: 865, longitude: 1321)> Size: 3GB
dask.array<transpose, shape=(324, 865, 1321), dtype=float64, chunksize=(1, 865, 1321), chunktype=numpy.ndarray>
Coordinates:
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
  * time       (time) datetime64[ns] 3kB 1993-01-16T12:00:00 ... 2019-12-16T1...
    depth      float64 8B 5.0
Attributes:
    standard_name:  sea_water_salinity
    long_name:      Salinity
    units:          1e-3
    unit_long:      Practical Salinity Unit
    cell_methods:   area: mean time: mean
    _ChunkSizes:    [  1   7 341 720]

In [10]:
# This basically just extracts the index of the first depth greater than 5.
# The > op returns an array of bools, and argmax returns the index of the 
# First true value in that array, since I guess "True" is the max value
dep_idx = np.argmax(pot_density.depth.values>5.0)
dep_idx

4

In [11]:
# For depths greater than 5, find index of first density who's value is >= the 5m density+0.03
# need to add dep_idx to the end since we subset(here) to values greater than this index 
#arg_max_vals = np.argmax( (pot_density.values[:,dep_idx:,:,:] >= (potdens_5m.values[:,np.newaxis,:,:]+0.03) ), axis=1 ) + dep_idx
arg_max_bool = pot_density >= (potdens_5m+0.03)
arg_max_vals = arg_max_bool.argmax(dim="depth")
arg_max_vals

<xarray.DataArray 'so' (time: 324, latitude: 865, longitude: 1321)> Size: 3GB
dask.array<arg_agg-aggregate, shape=(324, 865, 1321), dtype=int64, chunksize=(1, 865, 1321), chunktype=numpy.ndarray>
Coordinates:
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
  * time       (time) datetime64[ns] 3kB 1993-01-16T12:00:00 ... 2019-12-16T1...

In [12]:
arg_max_vals = arg_max_vals.expand_dims(dim={"depth":[None]},axis=1)
arg_max_vals

<xarray.DataArray 'so' (time: 324, depth: 1, latitude: 865, longitude: 1321)> Size: 3GB
dask.array<transpose, shape=(324, 1, 865, 1321), dtype=int64, chunksize=(1, 1, 865, 1321), chunktype=numpy.ndarray>
Coordinates:
  * depth      (depth) object 8B None
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
  * time       (time) datetime64[ns] 3kB 1993-01-16T12:00:00 ... 2019-12-16T1...

In [13]:
# Sum densities over all deptsh meeting the above critera?
depth_sum = arg_max_bool.sum(dim="depth")
depth_sum

<xarray.DataArray 'so' (time: 324, latitude: 865, longitude: 1321)> Size: 3GB
dask.array<sum-aggregate, shape=(324, 865, 1321), dtype=int64, chunksize=(1, 865, 1321), chunktype=numpy.ndarray>
Coordinates:
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
  * time       (time) datetime64[ns] 3kB 1993-01-16T12:00:00 ... 2019-12-16T1...

In [14]:
## Get argmax_vals, since we need it in memory to do the subsetting
#arg_max_vals = arg_max_vals.compute()

In [14]:
# Can't use dask arrays as indexers, so unfortunately no way to avoid computation in this step
dens_top = np.squeeze(np.take_along_axis(pot_density.values, (arg_max_vals.values-1), axis=1))
dens_bot = np.squeeze(np.take_along_axis(pot_density.values, (arg_max_vals.values), axis=1))

KilledWorker: Attempted to run task 'original-open_dataset-so-b036afa91f479f62cdae78474a56bba3' on 4 different workers, but all those workers died while running it. The last worker that attempt to run the task was tcp://140.208.147.21:38079. Inspecting worker logs is often a good next step to diagnose what went wrong. For more information see https://distributed.dask.org/en/stable/killed.html.

In [17]:
depth = pot_density.depth.values
z_top = (depth[arg_max_vals-1]).squeeze()
z_bot = (depth[arg_max_vals]).squeeze()
z_top.shape

(48, 865, 1321)

In [18]:
delta_dens = dens_bot-dens_top
delta_z = z_top - z_bot
delta_z.shape

(48, 865, 1321)

In [19]:
# calculating depth below upper layer given the slope, delta_dens/delta_z_l, between layers above and below
# rho@5m +0.03 kg/m3
mld = z_top + (((potdens_5m.values+0.03) - dens_top)/(delta_dens))*delta_z

In [21]:
# anywhere there were no depth layers that met the +0.03 criteria, set mld to bottom depth because 
# water column is effectively homogeonous with rho@5m
#mld[depth_sum==0] =  np.tile(bathym.values[np.newaxis,:,:],(mld.shape[0],1,1))[depth_sum==0]
mld[depth_sum==0] =  np.tile(bathym[np.newaxis,:,:],(mld.shape[0],1,1))[depth_sum==0]

In [22]:
#mld_ds = xr.Dataset(mld,dims=['time','latitude','longitude'],coords= {"time":pot_density.coords['time'],"latitude":pot_density.coords["latitude"],"longitude":pot_density.coords["longitude"]})
mld_ds = xr.Dataset(data_vars=dict(mld=(["time","latitude","longitude"],mld)), coords= {"time":g_ds.coords['time'],"latitude":g_ds.coords["latitude"],"longitude":g_ds.coords["longitude"]})
mld_ds

<xarray.Dataset> Size: 439MB
Dimensions:    (time: 48, latitude: 865, longitude: 1321)
Coordinates:
  * time       (time) datetime64[ns] 384B 1993-01-16T12:00:00 ... 1996-12-16T...
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
Data variables:
    mld        (time, latitude, longitude) float64 439MB 34.6 34.24 ... 17.18

In [23]:
# Calculate climatology
mld_climo = mld_ds.groupby("time.month").mean()
mld_climo

<xarray.Dataset> Size: 110MB
Dimensions:    (month: 12, latitude: 865, longitude: 1321)
Coordinates:
  * latitude   (latitude) float32 3kB 10.0 10.08 10.17 ... 81.83 81.92 82.0
  * longitude  (longitude) float32 5kB 150.0 150.1 150.2 ... 259.8 259.9 260.0
  * month      (month) int64 96B 1 2 3 4 5 6 7 8 9 10 11 12
Data variables:
    mld        (month, latitude, longitude) float64 110MB 34.72 34.63 ... 16.26

In [24]:
# save
mld_climo.to_netcdf("/work/Utheri.Wagura/NEP/plotting/Figure_4/GLORYS_MLD_003_1993-2019_clim.nc")

In [15]:
cluster.close()
client.close()